# This notebook is created for IBM Data Science Capstone course.

In [1]:
print ("Hello Capstone Project Course!")
print ("Written by Qiushan(Lillian) Li. With code from Week 3 lab on NY.")
print ("Created during the summer of 2020.")

Hello Capstone Project Course!
Written by Qiushan(Lillian) Li. With code from Week 3 lab on NY.
Created during the summer of 2020.


In [2]:
print ("This project explores the venues and crime data in Calgary Alberta Canada.")
print ("I used the FourSquare API and cluster technique to examine the venue data.")
print ("I mapped out the crime data based on sectors in the city, to see which sector would be safer to do business to live.")

This project explores the venues and crime data in Calgary Alberta Canada.
I used the FourSquare API and cluster technique to examine the venue data.
I mapped out the crime data based on sectors in the city, to see which sector would be safer to do business to live.


## 1. Download all the dependencies.

In [3]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

import matplotlib.pyplot as plt
import pylab as pl
%matplotlib inline

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    folium-0.5.0               |             py_0          45 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    ------------------------------------------------------------
                       

## Section 1: Explore Venues in Each Neighborhood

## 2. Read in the neiborhood data. Create and clean the dataframe.

I found the postal code data of Alberta from wikipedia. I saved it as csv file and imported into the code as a dataframe.

In [4]:
import types
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_8542f4effd29402091066f9dae523865 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='deleted',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_8542f4effd29402091066f9dae523865.get_object(Bucket='course9capstone-donotdelete-pr-cdi0dkhjipopoi',Key='CalgaryNeighborhoods.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df = pd.read_csv(body)
df.head()


Postal Code       Borough                                  Neighborhood  \
0         T1A  Medicine Hat                          Central Medicine Hat   
1         T2A       Calgary                Penbrooke Meadows, Marlborough   
2         T3A       Calgary  Dalhousie, Edgemont, Hamptons, Hidden Valley   
3         T4A       Airdrie                                  East Airdrie   
4         T5A      Edmonton              West Clareview, East Londonderry   

   Latitude    Longitude  
0  50.03646   -110.67925  
1  51.04968   -113.96432  
2  51.12606  -114.143158  
3  51.27245   -113.98698  
4   53.5899    -113.4413

List the unique boroughs to have a rough idea of the dataset.

In [5]:
df['Borough'].value_counts()

Edmonton                                                       39
Not assigned                                                   36
Calgary                                                        35
Sherwood Park                                                   6
Grande Prairie                                                  3
Medicine Hat                                                    3
Red Deer                                                        3
Lethbridge                                                      3
Fort McMurray                                                   3
Airdrie                                                         2
Leduc                                                           1
Redwood Meadows                                                 1
Camrose                                                         1
Lacombe                                                         1
Sturgeon County                                                 1
Blackfalds

Limit the dataframe to contain only the Calgary data.

In [6]:
df=df[df.Borough == 'Calgary']
df['Borough'].value_counts()

Calgary    35
Name: Borough, dtype: int64

In [7]:
df.head(40)

Postal Code  Borough                                       Neighborhood  \
1           T2A  Calgary                     Penbrooke Meadows, Marlborough   
2           T3A  Calgary       Dalhousie, Edgemont, Hamptons, Hidden Valley   
10          T2B  Calgary                     Forest Lawn, Dover, Erin Woods   
11          T3B  Calgary     Montgomery, Bowness, Silver Springs, Greenwood   
19          T2C  Calgary  Lynnwood Ridge, Ogden, Foothills Industrial, G...   
20          T3C  Calgary  Rosscarrock, Westgate, Wildwood, Shaganappi, S...   
28          T2E  Calgary                    Bridgeland, Greenview, Zoo, YYC   
29          T3E  Calgary           Lakeview, Glendale, Killarney, Glamorgan   
37          T2G  Calgary  Inglewood, Burnsland, Chinatown, East Victoria...   
38          T3G  Calgary  Hawkwood, Arbour Lake, Citadel, Ranchlands, Ro...   
46          T2H  Calgary                        Highfield, Burns Industrial   
47          T3H  Calgary  Discovery Ridge, Signal Hill, West Springs, Ch...   
55          T2J  Calgary    Queensland, Lake Bonavista, Willow Park, Acadia   
56          T3J  Calgary    Martindale, Taradale, Falconridge, Saddle Ridge   
64          T2K  Calgary                           Thorncliffe, Tuxedo Park   
65          T3K  Calgary  Sandstone, MacEwan Glen, Beddington, Harvest H...   
73          T2L  Calgary                  Brentwood, Collingwood, Nose Hill   
74          T3L  Calgary                              Tuscany, Scenic Acres   
82          T2M  Calgary          Mount Pleasant, Capitol Hill, Banff Trail   
83          T3M  Calgary                     Cranston, Auburn Bay, Mahogany   
91          T2N  Calgary         Kensington, Westmont, Parkdale, University   
92          T3N  Calgary                                  Northeast Calgary   
100         T2P  Calgary                         City Centre, Calgary Tower   
101         T3P  Calgary                                      Symons Valley   
109         T2R  Calgary                      Connaught, West Victoria Park   
110         T3R  Calgary                                  Northwest Calgary   
118         T2S  Calgary           Elbow Park, Britannia, Parkhill, Mission   
119         T3S  Calgary                                  Southeast Calgary   
127         T2T  Calgary     South Calgary (Altadore / Bankview / Richmond)   
136         T2V  Calgary  Oak Ridge, Haysboro, Kingsland, Kelvin Grove, ...   
145         T2W  Calgary                      Braeside, Cedarbrae, Woodbine   
154         T2X  Calgary                                Midnapore, Sundance   
162         T1Y  Calgary                   Rundle, Whitehorn, Monterey Park   
163         T2Y  Calgary          Millrise, Somerset, Bridlewood, Evergreen   
172         T2Z  Calgary  Douglas Glen, McKenzie Lake, Copperfield, East...   

     Latitude    Longitude  
1    51.04968   -113.96432  
2    51.12606  -114.143158  
10    51.0318    -113.9786  
11    51.0809    -114.1616  
19    50.9878    -114.0001  
20    51.0388     -114.098  
28    51.0632    -114.0614  
29    51.0227    -114.1342  
37    51.0415    -114.0599  
38    51.1147    -114.1796  
46    50.9857    -114.0631  
47    51.0566    -114.1815  
55    50.9693    -114.0514  
56    51.0999    -113.9422  
64    51.0857    -114.0714  
65     51.127    -114.0787  
73    51.0917    -114.1127  
74    51.1162    -114.2089  
82    51.0696    -114.0862  
83    50.8902    -113.9892  
91    51.0591    -114.1146  
92    51.1494    -114.0019  
100   51.0472    -114.0802  
101   51.1793    -114.1333  
109   51.0426    -114.0791  
110   51.1497    -114.2695  
118   51.0171    -114.0812  
119   50.9724    -113.9758  
127   51.0316    -114.0994  
136   50.9909     -114.074  
145   50.9604    -114.1001  
154   50.9204    -114.0674  
162   51.0759    -114.0015  
163   50.9093    -114.0721  
172   50.9023    -113.9873

In [8]:
df[df.Neighborhood == 'Not assigned']

Empty DataFrame
Columns: [Postal Code, Borough, Neighborhood, Latitude, Longitude]
Index: []

In [9]:
df.shape

(35, 5)

In [10]:
df.dtypes

Postal Code     object
Borough         object
Neighborhood    object
Latitude        object
Longitude       object
dtype: object

In [11]:
df["Latitude"] = df.Latitude.astype(float)
df["Longitude"] = df.Longitude.astype(float)
df.dtypes

Postal Code      object
Borough          object
Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 1 boroughs and 35 neighborhoods.


## 3. Analyze the neighborhoods in Calgary

Use geopy library to get the latitude and longitude values of Calgary.

In [13]:
address = 'Calgary, AB'

geolocator = Nominatim(user_agent="tr_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Calgary are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Calgary are 51.0534234, -114.0625892.


In [14]:
# create map of Calgary using latitude and longitude values
map_calgary = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_calgary)  
    
map_calgary

Define Foursquare Credentials and Version

In [ ]:
CLIENT_ID = 'deleted' # your Foursquare ID
CLIENT_SECRET = 'deleted' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Create a function to find venues in all the neighborhoods in Calgary

In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=700):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            5000)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Write the code to run the above function on each neighborhood and create a new dataframe called calgary_venues

In [17]:
calgary_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Penbrooke Meadows, Marlborough
Dalhousie, Edgemont, Hamptons, Hidden Valley
Forest Lawn, Dover, Erin Woods
Montgomery, Bowness, Silver Springs, Greenwood
Lynnwood Ridge, Ogden, Foothills Industrial, Great Plains
Rosscarrock, Westgate, Wildwood, Shaganappi, Sunalta
Bridgeland, Greenview, Zoo, YYC
Lakeview, Glendale, Killarney, Glamorgan
Inglewood, Burnsland, Chinatown, East Victoria Park, Saddledome
Hawkwood, Arbour Lake, Citadel, Ranchlands, Royal Oak, Rocky Ridge
Highfield, Burns Industrial
Discovery Ridge, Signal Hill, West Springs, Christie Estates, Patterson, Cougar Ridge
Queensland, Lake Bonavista, Willow Park, Acadia
Martindale, Taradale, Falconridge, Saddle Ridge
Thorncliffe, Tuxedo Park
Sandstone, MacEwan Glen, Beddington, Harvest Hills, Coventry Hills, Panorama Hills
Brentwood, Collingwood, Nose Hill
Tuscany, Scenic Acres
Mount Pleasant, Capitol Hill, Banff Trail
Cranston, Auburn Bay, Mahogany
Kensington, Westmont, Parkdale, University
Northeast Calgary
City Centre, Calgary To

Check the size of the resulting dataframe

In [18]:
print(calgary_venues.shape)
calgary_venues.head()

(696, 7)


Neighborhood  Neighborhood Latitude  \
0  Penbrooke Meadows, Marlborough               51.04968   
1  Penbrooke Meadows, Marlborough               51.04968   
2  Penbrooke Meadows, Marlborough               51.04968   
3  Penbrooke Meadows, Marlborough               51.04968   
4  Penbrooke Meadows, Marlborough               51.04968   

   Neighborhood Longitude                      Venue  Venue Latitude  \
0              -113.96432            TD Canada Trust       51.052399   
1              -113.96432                   7-Eleven       51.045519   
2              -113.96432                   7-Eleven       51.044357   
3              -113.96432  Gong Kee BBQ Noodle House       51.044477   
4              -113.96432              Pho Rang Dong       51.044656   

   Venue Longitude         Venue Category  
0      -113.970643                   Bank  
1      -113.957341      Convenience Store  
2      -113.969612      Convenience Store  
3      -113.968857           Noodle House  
4      -113.969383  Vietnamese Restaurant

Check how many venues were returned for each neighborhood

In [19]:
calgary_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Braeside, Cedarbrae, Woodbine                                          11   
Brentwood, Collingwood, Nose Hill                                       4   
Bridgeland, Greenview, Zoo, YYC                                        47   
City Centre, Calgary Tower                                             57   
Connaught, West Victoria Park                                         100   
Cranston, Auburn Bay, Mahogany                                          4   
Dalhousie, Edgemont, Hamptons, Hidden Valley                            4   
Discovery Ridge, Signal Hill, West Springs, Chr...                      5   
Douglas Glen, McKenzie Lake, Copperfield, East ...                     11   
Elbow Park, Britannia, Parkhill, Mission                                3   
Forest Lawn, Dover, Erin Woods                                         10   
Hawkwood, Arbour Lake, Citadel, Ranchlands, Roy...                      4   
Highfield, Burns Industrial                                            22   
Inglewood, Burnsland, Chinatown, East Victoria ...                     95   
Kensington, Westmont, Parkdale, University                              6   
Lakeview, Glendale, Killarney, Glamorgan                               14   
Lynnwood Ridge, Ogden, Foothills Industrial, Gr...                      5   
Martindale, Taradale, Falconridge, Saddle Ridge                         4   
Midnapore, Sundance                                                    19   
Millrise, Somerset, Bridlewood, Evergreen                              35   
Montgomery, Bowness, Silver Springs, Greenwood                         25   
Mount Pleasant, Capitol Hill, Banff Trail                              24   
Northeast Calgary                                                       4   
Northwest Calgary                                                       1   
Oak Ridge, Haysboro, Kingsland, Kelvin Grove, W...                     50   
Penbrooke Meadows, Marlborough                                          6   
Queensland, Lake Bonavista, Willow Park, Acadia                         7   
Rosscarrock, Westgate, Wildwood, Shaganappi, Su...                     39   
Rundle, Whitehorn, Monterey Park                                       29   
Sandstone, MacEwan Glen, Beddington, Harvest Hi...                     21   
South Calgary (Altadore / Bankview / Richmond)                         10   
Southeast Calgary                                                       3   
Symons Valley                                                           5   
Thorncliffe, Tuxedo Park                                                5   
Tuscany, Scenic Acres                                                   7   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Braeside, Cedarbrae, Woodbine                                           11   
Brentwood, Collingwood, Nose Hill                                        4   
Bridgeland, Greenview, Zoo, YYC                                         47   
City Centre, Calgary Tower                                              57   
Connaught, West Victoria Park                                          100   
Cranston, Auburn Bay, Mahogany                                           4   
Dalhousie, Edgemont, Hamptons, Hidden Valley                             4   
Discovery Ridge, Signal Hill, West Springs, Chr...                       5   
Douglas Glen, McKenzie Lake, Copperfield, East ...                      11   
Elbow Park, Britannia, Parkhill, Mission                                 3   
Forest Lawn, Dover, Erin Woods                                          10   
Hawkwood, Arbour Lake, Citadel, Ranchlands, Roy...                       4   
Highfield, Burns Industrial                                             22   
Inglewood, Burnsland, Chinatown,

In [20]:
print('There are {} uniques categories.'.format(len(calgary_venues['Venue Category'].unique())))

There are 162 uniques categories.


## 4. Summarize the venue information in each Neighborhood

In [21]:
# one hot encoding
calgary_onehot = pd.get_dummies(calgary_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
calgary_onehot['Neighborhood'] = calgary_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [calgary_onehot.columns[-1]] + list(calgary_onehot.columns[:-1])
calgary_onehot = calgary_onehot[fixed_columns]

calgary_onehot.head()

Neighborhood  Accessories Store  American Restaurant  \
0  Penbrooke Meadows, Marlborough                  0                    0   
1  Penbrooke Meadows, Marlborough                  0                    0   
2  Penbrooke Meadows, Marlborough                  0                    0   
3  Penbrooke Meadows, Marlborough                  0                    0   
4  Penbrooke Meadows, Marlborough                  0                    0   

   Art Gallery  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0            0                 0                   0                0   
1            0                 0                   0                0   
2            0                 0                   0                0   
3            0                 0                   0                0   
4            0                 0                   0                0   

   Automotive Shop  BBQ Joint  Bakery  Bank  Bar  Bistro  Board Shop  \
0                0          0       0     1    0       0           0   
1                0          0       0     0    0       0           0   
2                0          0       0     0    0       0           0   
3                0          0       0     0    0       0           0   
4                0          0       0     0    0       0           0   

   Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0          0         0              0                     0               0   
1          0         0              0                     0               0   
2          0         0              0                     0               0   
3          0         0              0                     0               0   
4          0         0              0                     0               0   

   Brewery  Building  Burger Joint  Bus Station  Bus Stop  Café  Camera Store  \
0        0         0             0            0         0     0             0   
1        0         0             0            0         0     0             0   
2        0         0             0            0         0     0             0   
3        0         0             0            0         0     0             0   
4        0         0             0            0         0     0             0   

   Candy Store  Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0            0                   0               0             0            0   
1            0                   0               0             0            0   
2            0                   0               0             0            0   
3            0                   0               0             0            0   
4            0                   0               0             0            0   

   Comedy Club  Comic Shop  Construction & Landscaping  Convenience Store  \
0            0           0                           0                  0   
1            0           0                           0                  1   
2            0           0                           0                  1   
3            0           0                           0                  0   
4            0           0                           0                  0   

   Cosmetics Shop  Dance Studio  Deli / Bodega  Department Store  \
0               0             0              0                 0   
1               0             0              0                 0   
2               0             0              0                 0   
3               0             0              0                 0   
4               0             0              0                 0   

   Dim Sum Restaurant  Diner  Discount Store  Donut Shop  Dry Cleaner  \
0                   0      0               0           0            0   
1                   0      0               0           0            0   
2                   0      0               0           0            0   
3                   0      0               0           0            0   


Examine the new dataframe size

In [22]:
calgary_onehot.shape

(696, 163)

Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [23]:
calgary_grouped = calgary_onehot.groupby('Neighborhood').mean().reset_index()
calgary_grouped

Neighborhood  Accessories Store  \
0                       Braeside, Cedarbrae, Woodbine               0.00   
1                   Brentwood, Collingwood, Nose Hill               0.00   
2                     Bridgeland, Greenview, Zoo, YYC               0.00   
3                          City Centre, Calgary Tower               0.00   
4                       Connaught, West Victoria Park               0.00   
5                      Cranston, Auburn Bay, Mahogany               0.00   
6        Dalhousie, Edgemont, Hamptons, Hidden Valley               0.00   
7   Discovery Ridge, Signal Hill, West Springs, Ch...               0.00   
8   Douglas Glen, McKenzie Lake, Copperfield, East...               0.00   
9            Elbow Park, Britannia, Parkhill, Mission               0.00   
10                     Forest Lawn, Dover, Erin Woods               0.00   
11  Hawkwood, Arbour Lake, Citadel, Ranchlands, Ro...               0.00   
12                        Highfield, Burns Industrial               0.00   
13  Inglewood, Burnsland, Chinatown, East Victoria...               0.00   
14         Kensington, Westmont, Parkdale, University               0.00   
15           Lakeview, Glendale, Killarney, Glamorgan               0.00   
16  Lynnwood Ridge, Ogden, Foothills Industrial, G...               0.00   
17    Martindale, Taradale, Falconridge, Saddle Ridge               0.00   
18                                Midnapore, Sundance               0.00   
19          Millrise, Somerset, Bridlewood, Evergreen               0.00   
20     Montgomery, Bowness, Silver Springs, Greenwood               0.04   
21          Mount Pleasant, Capitol Hill, Banff Trail               0.00   
22                                  Northeast Calgary               0.00   
23                                  Northwest Calgary               0.00   
24  Oak Ridge, Haysboro, Kingsland, Kelvin Grove, ...               0.00   
25                     Penbrooke Meadows, Marlborough               0.00   
26    Queensland, Lake Bonavista, Willow Park, Acadia               0.00   
27  Rosscarrock, Westgate, Wildwood, Shaganappi, S...               0.00   
28                   Rundle, Whitehorn, Monterey Park               0.00   
29  Sandstone, MacEwan Glen, Beddington, Harvest H...               0.00   
30     South Calgary (Altadore / Bankview / Richmond)               0.00   
31                                  Southeast Calgary               0.00   
32                                      Symons Valley               0.00   
33                           Thorncliffe, Tuxedo Park               0.00   
34                              Tuscany, Scenic Acres               0.00   

    American Restaurant  Art Gallery  Asian Restaurant  Athletics & Sports  \
0              0.000000     0.000000          0.000000                0.00   
1              0.000000     0.000000          0.000000                0.00   
2              0.000000     0.000000          0.021277                0.00   
3              0.000000     0.000000          0.000000                0.00   
4              0.000000     0.000000          0.000000                0.00   
5              0.000000     0.000000          0.000000                0.00   
6              0.000000     0.000000          0.250000                0.00   
7              0.000000     0.000000          0.000000                0.00   
8              0.000000     0.000000          0.090909                0.00   
9              0.000000     0.000000          0.000000                0.00   
10             0.000000     0.000000          0.000000                0.00   
11             0.000000     0.000000          0.000000                0.00   
12             0.090909     0.000000          0.000000                0.00   
13             0.021053     0.010526          0.021053                0.00   
14             0.000000     0.000000          0.000000                0.00   
15             0.000000     0.000000          0.000000  

Confirm the new size

In [24]:
calgary_grouped.shape

(35, 163)

Write a function to sort the venues in descending order

In [25]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create the new dataframe and display the top 10 venues for each neighborhood

In [26]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = calgary_grouped['Neighborhood']

for ind in np.arange(calgary_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(calgary_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head(40)

Neighborhood  1st Most Common Venue  \
0                       Braeside, Cedarbrae, Woodbine         Ice Cream Shop   
1                   Brentwood, Collingwood, Nose Hill               Building   
2                     Bridgeland, Greenview, Zoo, YYC            Coffee Shop   
3                          City Centre, Calgary Tower                    Bar   
4                       Connaught, West Victoria Park                    Pub   
5                      Cranston, Auburn Bay, Mahogany             Playground   
6        Dalhousie, Edgemont, Hamptons, Hidden Valley                   Café   
7   Discovery Ridge, Signal Hill, West Springs, Ch...            Pizza Place   
8   Douglas Glen, McKenzie Lake, Copperfield, East...            Dry Cleaner   
9            Elbow Park, Britannia, Parkhill, Mission            Bus Station   
10                     Forest Lawn, Dover, Erin Woods         Sandwich Place   
11  Hawkwood, Arbour Lake, Citadel, Ranchlands, Ro...            Pizza Place   
12                        Highfield, Burns Industrial    American Restaurant   
13  Inglewood, Burnsland, Chinatown, East Victoria...            Coffee Shop   
14         Kensington, Westmont, Parkdale, University              Gift Shop   
15           Lakeview, Glendale, Killarney, Glamorgan          Bowling Alley   
16  Lynnwood Ridge, Ogden, Foothills Industrial, G...                  Diner   
17    Martindale, Taradale, Falconridge, Saddle Ridge           Skating Rink   
18                                Midnapore, Sundance            Coffee Shop   
19          Millrise, Somerset, Bridlewood, Evergreen               Pharmacy   
20     Montgomery, Bowness, Silver Springs, Greenwood             Restaurant   
21          Mount Pleasant, Capitol Hill, Banff Trail            Coffee Shop   
22                                  Northeast Calgary    American Restaurant   
23                                  Northwest Calgary            Flea Market   
24  Oak Ridge, Haysboro, Kingsland, Kelvin Grove, ...           Burger Joint   
25                     Penbrooke Meadows, Marlborough      Convenience Store   
26    Queensland, Lake Bonavista, Willow Park, Acadia       Insurance Office   
27  Rosscarrock, Westgate, Wildwood, Shaganappi, S...                    Pub   
28                   Rundle, Whitehorn, Monterey Park    American Restaurant   
29  Sandstone, MacEwan Glen, Beddington, Harvest H...          Grocery Store   
30     South Calgary (Altadore / Bankview / Richmond)            Pizza Place   
31                                  Southeast Calgary        Automotive Shop   
32                                      Symons Valley             Restaurant   
33                           Thorncliffe, Tuxedo Park  Vietnamese Restaurant   
34                              Tuscany, Scenic Acres               Pharmacy   

     2nd Most Common Venue  3rd Most Common Venue       4th Most Common Venue  \
0                      Gym            Pizza Place                        Pool   
1              Hockey Rink    Sporting Goods Shop  Construction & Landscaping   
2             Noodle House    Japanese Restaurant          Chinese Restaurant   
3              Coffee Shop                    Pub           French Restaurant   
4               Restaurant                   Café                 Coffee Shop   
5           Cosmetics Shop           Liquor Store                 Pizza Place   
6              Gas Station       Asian Restaurant           Convenience Store   
7        Convenience Store                    Bar                 Gas Station   
8                      Pub            Golf Course                Soccer Field   
9                     Park    Japanese Restaurant                  Food Truck   
10       Convenience Store                    Bar       Vietnamese Restaurant   
11                     Pub      Convenience Store                 Yoga Studio   
12  Furniture / Home Store            Gas Station          Mexican Restaurant   
13                   Hotel

## 5. Cluster Neighborhoods based on Venue Information

Run k-means to cluster the neighborhood into 10 clusters

In [27]:
# set number of clusters
kclusters = 10

calgary_grouped_clustering = calgary_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(calgary_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:40] 


array([0, 5, 0, 0, 0, 6, 2, 2, 0, 3, 2, 4, 0, 0, 7, 0, 0, 9, 0, 0, 0, 0,
       0, 1, 0, 2, 0, 0, 0, 0, 0, 8, 0, 2, 0], dtype=int32)

Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood

In [28]:
# add clustering labels

if 'Cluster Labels' in neighborhoods_venues_sorted.columns:
    neighborhoods_venues_sorted = neighborhoods_venues_sorted.drop(['Cluster Labels'], axis=1)
    
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

calgary_merged = df

# merge calgary_grouped with df to add latitude/longitude for each neighborhood
calgary_merged = calgary_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

calgary_merged.head(40) # check the last columns!

Postal Code  Borough                                       Neighborhood  \
1           T2A  Calgary                     Penbrooke Meadows, Marlborough   
2           T3A  Calgary       Dalhousie, Edgemont, Hamptons, Hidden Valley   
10          T2B  Calgary                     Forest Lawn, Dover, Erin Woods   
11          T3B  Calgary     Montgomery, Bowness, Silver Springs, Greenwood   
19          T2C  Calgary  Lynnwood Ridge, Ogden, Foothills Industrial, G...   
20          T3C  Calgary  Rosscarrock, Westgate, Wildwood, Shaganappi, S...   
28          T2E  Calgary                    Bridgeland, Greenview, Zoo, YYC   
29          T3E  Calgary           Lakeview, Glendale, Killarney, Glamorgan   
37          T2G  Calgary  Inglewood, Burnsland, Chinatown, East Victoria...   
38          T3G  Calgary  Hawkwood, Arbour Lake, Citadel, Ranchlands, Ro...   
46          T2H  Calgary                        Highfield, Burns Industrial   
47          T3H  Calgary  Discovery Ridge, Signal Hill, West Springs, Ch...   
55          T2J  Calgary    Queensland, Lake Bonavista, Willow Park, Acadia   
56          T3J  Calgary    Martindale, Taradale, Falconridge, Saddle Ridge   
64          T2K  Calgary                           Thorncliffe, Tuxedo Park   
65          T3K  Calgary  Sandstone, MacEwan Glen, Beddington, Harvest H...   
73          T2L  Calgary                  Brentwood, Collingwood, Nose Hill   
74          T3L  Calgary                              Tuscany, Scenic Acres   
82          T2M  Calgary          Mount Pleasant, Capitol Hill, Banff Trail   
83          T3M  Calgary                     Cranston, Auburn Bay, Mahogany   
91          T2N  Calgary         Kensington, Westmont, Parkdale, University   
92          T3N  Calgary                                  Northeast Calgary   
100         T2P  Calgary                         City Centre, Calgary Tower   
101         T3P  Calgary                                      Symons Valley   
109         T2R  Calgary                      Connaught, West Victoria Park   
110         T3R  Calgary                                  Northwest Calgary   
118         T2S  Calgary           Elbow Park, Britannia, Parkhill, Mission   
119         T3S  Calgary                                  Southeast Calgary   
127         T2T  Calgary     South Calgary (Altadore / Bankview / Richmond)   
136         T2V  Calgary  Oak Ridge, Haysboro, Kingsland, Kelvin Grove, ...   
145         T2W  Calgary                      Braeside, Cedarbrae, Woodbine   
154         T2X  Calgary                                Midnapore, Sundance   
162         T1Y  Calgary                   Rundle, Whitehorn, Monterey Park   
163         T2Y  Calgary          Millrise, Somerset, Bridlewood, Evergreen   
172         T2Z  Calgary  Douglas Glen, McKenzie Lake, Copperfield, East...   

     Latitude   Longitude  Cluster Labels  1st Most Common Venue  \
1    51.04968 -113.964320               2      Convenience Store   
2    51.12606 -114.143158               2                   Café   
10   51.03180 -113.978600               2         Sandwich Place   
11   51.08090 -114.161600               0             Restaurant   
19   50.98780 -114.000100               0                  Diner   
20   51.03880 -114.098000               0                    Pub   
28   51.06320 -114.061400               0            Coffee Shop   
29   51.02270 -114.134200               0          Bowling Alley   
37   51.04150 -114.059900               0            Coffee Shop   
38   51.11470 -114.179600               4            Pizza Place   
46   50.98570 -114.063100               0    American Restaurant   
47   51.05660 -114.181500               2            Pizza Place   
55   50.96930 -114.051400               0       Insurance Office   
56   51.09990 -113.942200               9           Skating Rink   
64   51.08570 -114.071400               2  Vietnamese Restaurant   
65   51.12700 -114.078700               0          Grocery Store   
73 

Visualize the resulting clusters

In [29]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(calgary_merged['Latitude'], calgary_merged['Longitude'], calgary_merged['Neighborhood'], calgary_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 5. Examine the 10 Neighborhoods

In [30]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 0, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
11   Calgary               0            Restaurant          Clothing Store   
19   Calgary               0                 Diner                 Theater   
20   Calgary               0                   Pub      Mexican Restaurant   
28   Calgary               0           Coffee Shop            Noodle House   
29   Calgary               0         Bowling Alley          Sandwich Place   
37   Calgary               0           Coffee Shop                   Hotel   
46   Calgary               0   American Restaurant  Furniture / Home Store   
55   Calgary               0      Insurance Office      Miscellaneous Shop   
65   Calgary               0         Grocery Store                    Bank   
74   Calgary               0              Pharmacy            Skating Rink   
82   Calgary               0           Coffee Shop          Sandwich Place   
92   Calgary               0   American Restaurant             Gas Station   
100  Calgary               0                   Bar             Coffee Shop   
101  Calgary               0            Restaurant            Home Service   
109  Calgary               0                   Pub              Restaurant   
127  Calgary               0           Pizza Place            Liquor Store   
136  Calgary               0          Burger Joint          Clothing Store   
145  Calgary               0        Ice Cream Shop                     Gym   
154  Calgary               0           Coffee Shop             Pizza Place   
162  Calgary               0   American Restaurant                   Hotel   
163  Calgary               0              Pharmacy             Coffee Shop   
172  Calgary               0           Dry Cleaner                     Pub   

    3rd Most Common Venue    4th Most Common Venue  \
11            Coffee Shop                     Park   
19      Convenience Store           Clothing Store   
20      Indian Restaurant    Vietnamese Restaurant   
28    Japanese Restaurant       Chinese Restaurant   
29            Coffee Shop      Japanese Restaurant   
37             Restaurant                      Pub   
46            Gas Station       Mexican Restaurant   
55     Chinese Restaurant        Convenience Store   
65           Liquor Store              Coffee Shop   
74                   Park              Video Store   
82     Chinese Restaurant         Sushi Restaurant   
92                  Hotel              Coffee Shop   
100                   Pub        French Restaurant   
101        Farmers Market        Convenience Store   
109                  Café              Coffee Shop   
127             Pet Store              Candy Store   
136            Steakhouse  New American Restaurant   
145           Pizza Place                     Pool   
154    Light Rail Station                Pet Store   
162     Indian Restaurant            Grocery Store   
163             Pet Store                      Pub   
172           Golf Course             Soccer Field   

          5th Most Common Venue    6th Most Common Venue  \
11            Accessories Store           Cosmetics Shop   
19                  Pizza Place             Home Service   
20                  Pizza Place           Sandwich Place   
28               Sandwich Place    Vietnamese Restaurant   
29                   Sports Bar              Supermarket   
37                      Theater               Steakhouse   
46             Sushi Restaurant              Coffee Shop   
55   Construction & Landscaping              Pizza Place   
65           Chinese Restaurant           Discount Store   
74            Convenience Store                      Pub   
82                          Pub                 Boutique   
92                  Yoga Studio               Food Truck   
100    Mediterranean Restaurant               Steakhouse   
101                 Coffee Shop              Yoga Studio   
109                         Bar       Italian Restaurant   
127    

In [31]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 1, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
110  Calgary               1           Flea Market           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
110            Food Truck             Gastropub           Gas Station   

      6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
110  Furniture / Home Store    Frozen Yogurt Shop   Fried Chicken Joint   

    9th Most Common Venue 10th Most Common Venue  
110     French Restaurant                 Forest

In [32]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 2, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels  1st Most Common Venue 2nd Most Common Venue  \
1   Calgary               2      Convenience Store                  Bank   
2   Calgary               2                   Café           Gas Station   
10  Calgary               2         Sandwich Place     Convenience Store   
47  Calgary               2            Pizza Place     Convenience Store   
64  Calgary               2  Vietnamese Restaurant        Ice Cream Shop   

    3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
1   Vietnamese Restaurant           Noodle House          Grocery Store   
2        Asian Restaurant      Convenience Store            Yoga Studio   
10                    Bar  Vietnamese Restaurant  Indonesian Restaurant   
47                    Bar            Gas Station  Vietnamese Restaurant   
64      Convenience Store            Coffee Shop                    Bar   

   6th Most Common Venue   7th Most Common Venue   8th Most Common Venue  \
1      Food & Drink Shop  Furniture / Home Store      Frozen Yogurt Shop   
2             Food Truck  Furniture / Home Store      Frozen Yogurt Shop   
10            Smoke Shop      Falafel Restaurant     Fried Chicken Joint   
47           Dry Cleaner       Food & Drink Shop  Furniture / Home Store   
64           Yoga Studio       Food & Drink Shop  Furniture / Home Store   

   9th Most Common Venue  10th Most Common Venue  
1    Fried Chicken Joint       French Restaurant  
2    Fried Chicken Joint       French Restaurant  
10     Food & Drink Shop  Furniture / Home Store  
47    Frozen Yogurt Shop     Fried Chicken Joint  
64    Frozen Yogurt Shop     Fried Chicken Joint

In [33]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 3, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
118  Calgary               3           Bus Station                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
118   Japanese Restaurant            Food Truck             Gastropub   

    6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
118           Gas Station  Furniture / Home Store    Frozen Yogurt Shop   

    9th Most Common Venue 10th Most Common Venue  
118   Fried Chicken Joint      French Restaurant

In [34]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 4, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
38  Calgary               4           Pizza Place                   Pub   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
38     Convenience Store           Yoga Studio           Flea Market   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
38  Furniture / Home Store    Frozen Yogurt Shop   Fried Chicken Joint   

   9th Most Common Venue 10th Most Common Venue  
38     French Restaurant                 Forest

In [35]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 5, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
73  Calgary               5              Building           Hockey Rink   

   3rd Most Common Venue       4th Most Common Venue 5th Most Common Venue  \
73   Sporting Goods Shop  Construction & Landscaping     Food & Drink Shop   

   6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
73           Gas Station  Furniture / Home Store    Frozen Yogurt Shop   

   9th Most Common Venue 10th Most Common Venue  
73   Fried Chicken Joint      French Restaurant

In [36]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 6, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
83  Calgary               6            Playground        Cosmetics Shop   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
83          Liquor Store           Pizza Place  Eastern European Restaurant   

   6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
83            Food Truck  Furniture / Home Store    Frozen Yogurt Shop   

   9th Most Common Venue 10th Most Common Venue  
83   Fried Chicken Joint      French Restaurant

In [37]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 7, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
91  Calgary               7             Gift Shop  Furniture / Home Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
91         Deli / Bodega          Dance Studio        Massage Studio   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
91            Hobby Shop     Food & Drink Shop    Frozen Yogurt Shop   

   9th Most Common Venue 10th Most Common Venue  
91   Fried Chicken Joint      French Restaurant

In [38]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 8, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
119  Calgary               8       Automotive Shop        Rental Service   

    3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
119           Flea Market           Gas Station  Furniture / Home Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
119    Frozen Yogurt Shop   Fried Chicken Joint     French Restaurant   

    9th Most Common Venue 10th Most Common Venue  
119                Forest             Food Truck

In [39]:
calgary_merged.loc[calgary_merged['Cluster Labels'] == 9, calgary_merged.columns[[1] + list(range(5, calgary_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
56  Calgary               9          Skating Rink     Convenience Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
56  Fast Food Restaurant        Sandwich Place            Food Truck   

   6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
56           Gas Station  Furniture / Home Store    Frozen Yogurt Shop   

   9th Most Common Venue 10th Most Common Venue  
56   Fried Chicken Joint      French Restaurant

## Section 2: Explore Crime Data in Each Sector

## 6. Import and Explore the Neighborhood Map and Crime Data

I obtained official crime map datasets from https://data.calgary.ca/.

In [40]:
calgary_geo = 'https://data.calgary.ca/resource/78gh-n26t.geojson'

calgary_geo

'https://data.calgary.ca/resource/78gh-n26t.geojson'

In [41]:
crime_map = folium.Map(
    location=[51.0534234, -114.0625892],
)
crime_map

In [42]:
folium.GeoJson(
    calgary_geo,
    name ='CalgaryCrime'
).add_to(crime_map)

In [43]:
crime_map

Import the crime data as a dataframe.

In [73]:
body = client_8542f4effd29402091066f9dae523865.get_object(Bucket='course9capstone-donotdelete-pr-cdi0dkhjipopoi',Key='Community_Crime_Statistics.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_crime = pd.read_csv(body)
df_crime.head()


Sector Community Name                Category  Crime Count  \
0  NORTHWEST            02E  Assault (Non-domestic)            6   
1       WEST    ASPEN WOODS          Street Robbery            1   
2     CENTRE   CAPITOL HILL          Street Robbery            1   
3     CENTRE       HIGHWOOD  Assault (Non-domestic)            1   
4      NORTH            02K        Theft OF Vehicle            1   

   Resident Count                    Date  Year Month        long        lat  \
0             0.0  05/01/2020 12:00:00 AM  2020   MAY -114.199362  51.161431   
1          9446.0  05/01/2020 12:00:00 AM  2020   MAY -114.207876  51.045131   
2          4744.0  07/01/2020 12:00:00 AM  2020   JUL -114.094652  51.072662   
3          2258.0  07/01/2020 12:00:00 AM  2020   JUL -114.079901  51.092356   
4             0.0  04/01/2020 12:00:00 AM  2020   APR -114.180588  51.190427   

                                         ID  \
0       2020-MAY-02E-Assault (Non-domestic)   
1       2020-MAY-ASPEN WOODS-Street Robbery   
2      2020-JUL-CAPITOL HILL-Street Robbery   
3  2020-JUL-HIGHWOOD-Assault (Non-domestic)   
4             2020-APR-02K-Theft OF Vehicle   

                      Community Center Point  
0  POINT (-114.199362020526 51.161430618799)  
1  POINT (-114.207876270297 51.045130968851)  
2  POINT (-114.094651621635 51.072661693566)  
3   POINT (-114.07990104744 51.092355774905)  
4  POINT (-114.180588398906 51.190427466876)

In [74]:
df_crime.shape

(41561, 12)

In [75]:
df_crime.dropna(subset = ["long"], inplace=True)
df_crime.dropna(subset = ["lat"], inplace=True)

In [76]:
df_crime.shape

(41409, 12)

In [77]:
df_crime.describe()

Crime Count  Resident Count          Year          long           lat
count  41409.000000    41409.000000  41409.000000  41409.000000  41409.000000
mean       3.040185     6534.775049   2018.340868   -114.061912     51.042425
std        3.980679     5404.621695      1.048750      0.077845      0.070889
min        1.000000        0.000000   2017.000000   -114.286695     50.854445
25%        1.000000     2359.000000   2017.000000   -114.115129     51.003089
50%        2.000000     5957.000000   2018.000000   -114.066709     51.047969
75%        4.000000     9338.000000   2019.000000   -113.996784     51.088795
max      110.000000    25925.000000   2020.000000   -113.871525     51.197958

In [67]:
df_category=df_crime.groupby("Category")["Crime Count"].sum().to_frame('Total').reset_index()
df_category

Category  Total
0           Assault (Non-domestic)  13064
1       Break & Enter - Commercial  17879
2         Break & Enter - Dwelling   8468
3   Break & Enter - Other Premises   7668
4               Commercial Robbery   1148
5                   Street Robbery   2105
6               Theft FROM Vehicle  47213
7                 Theft OF Vehicle  20905
8  Violence 'Other' (Non-domestic)    974
9    Violence Other (Non-domestic)   6467

In [68]:
# get the first 1000 crimes in the df_crime dataframe
limit = 1000
df_crime = df_crime.iloc[0:limit, :]

In [69]:
df_crime.shape

(1000, 12)

Create a dataframe for sector information to create a choropleth map.

In [70]:
desc = df_crime["Sector"].describe() 
desc

count       1000
unique         8
top       CENTRE
freq         258
Name: Sector, dtype: object

In [71]:
df_category=df_crime.groupby("Category")["Crime Count"].sum().to_frame('Total').reset_index()
df_category

Category  Total
0          Assault (Non-domestic)    156
1      Break & Enter - Commercial    266
2        Break & Enter - Dwelling     73
3  Break & Enter - Other Premises    107
4              Commercial Robbery      8
5                  Street Robbery     28
6              Theft FROM Vehicle    611
7                Theft OF Vehicle    276
8   Violence Other (Non-domestic)    808

In [72]:
df_sector=df_crime.groupby("Sector")["Crime Count"].sum().to_frame('Total').reset_index()
df_sector

Sector  Total
0     CENTRE    883
1       EAST    205
2      NORTH    199
3  NORTHEAST    295
4  NORTHWEST    192
5      SOUTH    325
6  SOUTHEAST    122
7       WEST    112

In [52]:
# Create a crime map of Calgary
crime_map = folium.Map(
    location=[51.0534234, -114.0625892],
)
crime_map

In [53]:
# To add labelson the map, instantiate a feature group for the incidents in the dataframe
incidents = folium.map.FeatureGroup()

# add pop-up text to each marker on the map
latitudes = list(df_crime.lat)
longitudes = list(df_crime.long)
labels = list(df_crime.Category)

for lat, lng, label in zip(latitudes, longitudes, labels):
    folium.Marker([lat, lng], popup=label).add_to(crime_map)    
    
# add incidents to map
crime_map.add_child(incidents)
crime_map

In [54]:
from folium import plugins

# let's start again with a clean copy of the map of San Francisco
crime_map = folium.Map(location = [latitude, longitude], zoom_start = 10)

# instantiate a mark cluster object for the incidents in the dataframe
incidents = plugins.MarkerCluster().add_to(crime_map)

# loop through the dataframe and add each data point to the mark cluster
for lat, long, label, in zip(df_crime.lat, df_crime.long, df_crime.Category):
    folium.Marker(
        location=[lat, long],
        icon=None,
        popup=label,
    ).add_to(incidents)

# display map
crime_map

## 7. Choropleth Map based on Sector

I obtained official city sector map geojson from https://data.calgary.ca/.

In [55]:
sector_geo = 'https://data.calgary.ca/api/geospatial/mz2j-7eb5?method=export&format=GeoJSON'

sector_geo

'https://data.calgary.ca/api/geospatial/mz2j-7eb5?method=export&format=GeoJSON'

In [56]:
sector_map = folium.Map(
    location=[51.0534234, -114.0625892],
)

In [57]:
folium.GeoJson(
    sector_geo,
    name ='CalgaryCrimeSector'
).add_to(sector_map)

In [58]:
sector_map

In [59]:
# generate choropleth map
sector_map.choropleth(
    geo_data=sector_geo,
    data=df_sector,
    columns=['Sector', 'Total'],
    key_on='feature.properties.sector',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Choropleth Map'
)

# display map
sector_map